In [1]:
import copy
from cycler import cycler
import os.path

import numpy as np
import matplotlib as mpl
import matplotlib.pyplot as plt
import pandas as pd
import plotly.graph_objects as go

import results_config as config

In [2]:
%matplotlib inline
plt.style.use('driver_cuda.mplstyle')
mpl.rcParams['axes.prop_cycle'] = cycler(color=['#ea4335', '#4285f4', 'g', 'y'])
titleFondDic = {"size":40, "weight":"bold", "color":'#1c4587'}

#ea4335
#4285f4

# plt.rcParams.update({'figure.figsize':(8,8), 'figure.dpi':600})

GPU = {
    'p3.2xlarge' : 'V100',
    'p2.xlarge' : 'K80',
    't4' : 'Tesla T4 (n1-standard-8)',
    'g3.4xlarge' : 'M60',
}

In [3]:
df = pd.read_csv(config.data_file)

In [4]:
menu_instance = {
    ("v100","n1-standard-4") : 1.87,
    ("v100","n1-standard-8") : 2.003,
    ("v100","n1-standard-12") : 2.156,
    ("p100","n1-standard-4"): 1.156,
    ("p100","n1-standard-8"): 1.289,
    ("p100","n1-standard-12"): 1.442,
    ("p4","n1-standard-4"): 0.554,
    ("p4","n1-standard-8"): 0.554,
    ("p4","n1-standard-12"): 0.84,
    ("t4","n1-standard-4"): 0.379,
    ("t4","n1-standard-8"): 0.379,
    ("t4","n1-standard-12"): 0.665,
    ("k80","n1-standard-4"): 0.449,
}

In [5]:
def get_waterfall_data(dataframe, column):
    max_val = dataframe[column][0:1][0]
    return dataframe[column].diff(periods=1).fillna(value=max_val).div(max_val/100)

def price(gpu):
    for key, value in menu_instance.items():
        if (key[0] in gpu) and (key[1][-1:] == gpu[-1:]):
            return value

def transform_df(df):
    # df['proc'] = df['adv_job_params'].apply(lambda x: int(x[-2:]))
    # df['batch'] = df['adv_job_params'].apply(lambda x: int(x[13:-20]))
    df["label"] = df[["gpu_type", "batch_size", "procs", "vCPU"]].apply(lambda x: f"{x[0]}_{x[1]}x{x[2]}_{x[3]}", axis=1)
    return df
    
def argsort(arr):
    return sorted(range(len(arr)), key=arr.__getitem__, reverse=True)

def diff(arr):
    result = []
    for i in range(len(arr)):
        if i > 0:
            result.append(arr[i] - arr[i-1])
        else:
            result.append(arr[i])
    return result

def build_graph(order, values, title, filename):
    order_int = copy.deepcopy(order)
    order_int.append("Minimal")
    values.append(0)
    text = [f"{values[i]:.0f}" for i in range(len(values)-1)] + [f"{sum(values):.0f}"]
    fig = go.Figure(go.Waterfall(
        name = 'runtime',
        orientation = 'v',
        measure = ["relative"]*(len(order_int)-1) + ["total"],
        x = order_int,
        textposition = 'outside',
        text = text,
        y = values,
        connector = {"line":{"color":"rgb(63,63,63)"}},
    ))

    fig.update_layout(
            title = title,
    )

    fig.show()
    fig.write_image(os.path.join(config.img_dir, f"{filename}.png"),width=600, height=350, scale=5)

def build_graph_w_cost(order, values, costs, title, filename):
    order_int = copy.deepcopy(order)
    order_int.append("Fastest")
    values.append(0)
    costs.append(0)
    text = [f"{values[i]:.0f}" for i in range(len(values)-1)] + [f"{sum(values):.0f}"]
    text_costs = [f"{costs[i]:.0f}" for i in range(len(costs)-1)] + [f"{sum(costs):.0f}"]

    fig = go.Figure()
    fig.add_trace(go.Waterfall(
        name = 'runtime (%)',
        orientation = 'v',
        measure = ["relative"]*(len(order_int)-1) + ["total"],
        x = order_int,
        textposition = 'outside',
        text = text,
        y = values,
        connector = {"line":{"color":"rgb(63,63,63)"}},
    ))

    fig.add_trace(go.Waterfall(
        name = 'cost (%)',
        orientation = 'v',
        measure = ["relative"]*(len(order_int)-1) + ["total"],
        x = order_int,
        textposition = 'outside',
        text = text_costs,
        y = costs,
        connector = {"line":{"color":"rgb(63,63,63)"}},
        decreasing = {"marker":{"color":"Maroon", "line":{"color":"red", "width":2}}},
        increasing = {"marker":{"color":"Teal"}},
        totals = {"marker":{"color":"deep sky blue", "line":{"color":"blue", "width":3}}}
    ))

    fig.update_layout(
            title = title,
            waterfallgroupgap = 0.2,
    )

    fig.show()
    fig.write_image(os.path.join(config.img_dir, f"{filename}.png"),width=600, height=350, scale=5)

def build_bar_graph(order, values, title, filename):
    text = [f"{values[i]:.0f}" for i in range(len(values))]

    fig = go.Figure(data=[
        go.Bar(name='Runtime', x=order, text=text, textposition='auto', y=values)
    ])
    # Change the bar mode
    fig.update_layout(title = title)
    fig.show()
    fig.write_image(os.path.join(config.img_dir, filename),width=600, height=350, scale=5)

def build_bar_graph_w_cost(order, values, costs, title, filename):
    text = [f"{values[i]:.0f}" for i in range(len(values))]
    text_costs = [f"{costs[i]:.0f}" for i in range(len(costs))]

    fig = go.Figure(data=[
        go.Bar(name='Runtime (%)', x=order, text=text, textposition='auto', y=values),
        go.Bar(name='Costs (%)', x=order, text=text_costs, textposition='auto', y=costs)
    ])
    # Change the bar mode
    fig.update_layout(title = title,barmode='group')
    fig.show()
    fig.write_image(os.path.join(config.img_dir, filename),width=600, height=350, scale=5)

In [6]:
df = transform_df(df)
df_perf = df[["label","gpu_type", "batch_size", "procs", "vCPU",'machine_type','CUDA','nvidia_driver_major','runtime']][(df['nvidia_driver_major']==460)  & (df["CUDA"]=='cu11.0') ]
df_perf

label gpu_type  batch_size  procs  vCPU    machine_type    CUDA  \
0       t4_100x2_4       t4         100      2     4   n1-standard-4  cu11.0   
1     v100_100x2_4     v100         100      2     4   n1-standard-4  cu11.0   
2      k80_100x2_4      k80         100      2     4   n1-standard-4  cu11.0   
3        p4_50x2_4       p4          50      2     4   n1-standard-4  cu11.0   
4      v100_75x2_4     v100          75      2     4   n1-standard-4  cu11.0   
..             ...      ...         ...    ...   ...             ...     ...   
71        p4_1x1_8       p4           1      1     8   n1-standard-8  cu11.0   
72        t4_1x1_8       t4           1      1     8   n1-standard-8  cu11.0   
73      v100_1x1_8     v100           1      1     8   n1-standard-8  cu11.0   
75       k80_1x1_8      k80           1      1     8   n1-standard-8  cu11.0   
93  p100_145x12_12     p100         145     12    12  n1-standard-12  cu11.0   

    nvidia_driver_major     runtime  
0                   460   738.72296  
1                   460   738.85490  
2                   460   832.09860  
3                   460   711.99480  
4                   460   706.96260  
..                  ...         ...  
71                  460  1610.00130  
72                  460  1943.50380  
73                  460  2023.38240  
75                  460  2597.18900  
93                  460   220.28017  

[70 rows x 9 columns]

In [7]:
price('k80_1x1_4')

0.449

In [8]:
p4 = df_perf[df_perf['gpu_type'] == 'p4'].sort_values(by='runtime',ascending=False)
p4.groupby('label').mean().sort_values(by='runtime',ascending=False)

batch_size  procs  vCPU  nvidia_driver_major     runtime
label                                                              
p4_1x2_4            1      2     4                  460  1898.29040
p4_1x1_8            1      1     8                  460  1610.00130
p4_5x2_4            5      2     4                  460   880.54740
p4_10x2_4          10      2     4                  460   792.44040
p4_15x2_4          15      2     4                  460   758.15180
p4_20x2_4          20      2     4                  460   738.03375
p4_63x2_4          63      2     4                  460   723.33880
p4_25x2_4          25      2     4                  460   722.85450
p4_50x2_4          50      2     4                  460   711.99480
p4_63x4_4          63      4     4                  460   562.25350
p4_63x6_4          63      6     4                  460   554.97550
p4_63x6_8          63      6     8                  460   460.43274
p4_63x8_8          63      8     8                  460   456.64820

In [9]:
mean = df_perf.groupby('label').mean().sort_values(by='runtime', ascending=False)
mean

batch_size  procs  vCPU  nvidia_driver_major     runtime
label                                                                   
k80_1x2_4                1      2     4                  460  2688.92530
k80_1x1_8                1      1     8                  460  2597.18900
p100_1x2_4               1      2     4                  460  2568.48560
t4_1x2_4                 1      2     4                  460  2232.65040
v100_1x2_4               1      2     4                  460  2096.78170
...                    ...    ...   ...                  ...         ...
p100_146x8_8           146      8     8                  460   334.68970
v100_145x6_8           145      6     8                  460   322.00473
v100_145x8_8           145      8     8                  460   289.42952
p100_145x12_12         145     12    12                  460   220.28017
v100_145x12_12         145     12    12                  460   201.04420

[66 rows x 5 columns]

In [10]:
mean.filter(regex= 'k80.*4$', axis=0).sort_values(by='runtime', ascending=False).runtime[0]

2688.9253

In [11]:
#

In [12]:
#

In [13]:
single = mean.filter(regex= '.*_1x2.*', axis=0).sort_values(by='runtime', ascending=False)
s_order = single.index
s_values = get_waterfall_data(single, 'runtime')
build_graph(list(s_order), list(s_values), "Single Article Runtume Waterfall", "single")

In [14]:
s_order

Index(['k80_1x2_4', 'p100_1x2_4', 't4_1x2_4', 'v100_1x2_4', 'p4_1x2_4'], dtype='object', name='label')

In [15]:
s_order = list(s_order)
s_values = list(single.runtime)
max_val = max(s_values)
s_costs = []
for i, gpu in enumerate(s_order):
    s_costs.append(s_values[i]*price(gpu)/3600)
    s_order[i] = s_order[i]

max_costs = max(s_costs)

s_costs = [c * 100 / max_costs for c in s_costs]
s_values = [c *100 / max_val for c in s_values]


In [16]:
s_values

[100.0,
 95.52089825626618,
 83.03132853858008,
 77.97842877970616,
 70.59662088790641]

In [17]:
s_costs

[30.79145805181259,
 75.72515050955558,
 21.580679260789804,
 100.0,
 26.82116216995561]

In [18]:
s_order

['k80_1x2_4', 'p100_1x2_4', 't4_1x2_4', 'v100_1x2_4', 'p4_1x2_4']

In [19]:
build_bar_graph_w_cost(s_order, s_values, s_costs, "Single Article: Runtume vs Cost", "single_bars.png")

## Single Article Performance

In [20]:
for gpu in ["k80", "p4", "p100",  "v100", "t4"]:
    data = mean.filter(like = gpu, axis=0).sort_values(by='runtime', ascending=False)
    gpu_order = list(data.index)
    gpu_values = list(data.runtime)
    build_bar_graph(list(gpu_order), list(gpu_values), f"Tesla {gpu} Runtume (sec)", f"{gpu}_bar.png")

## Optimized Performance

In [21]:
opt_order = []
opt_values = []
opt_costs = []
for gpu in ['k80.*4$', "p4.*4$","p4.*8$", "p100.*4$", "p100.*8$", "p100.*12$", "v100.*4$", "v100.*8$", "v100.*12$", "t4.*4$", "t4.*8$"]:
    opt_values.append(mean.filter(regex=gpu, axis=0).sort_values(by='runtime').runtime[0])
    instance = mean.filter(regex=gpu, axis=0).sort_values(by='runtime').index[0]
    opt_order.append(instance)
    opt_costs.append(price(instance)*opt_values[-1]/3600)
# build_graph(list(gpu_order), list(gpu_values), f"Tesla {gpu} Runtume Waterfall", gpu)

In [22]:
sort_opt_order = []
sort_opt_values = []
sort_opt_costs = []
absolute_max_val = max(opt_values) / 100
absolute_max_cost = max(opt_costs) / 100
for i in argsort(opt_values):
    sort_opt_order.append(opt_order[i])
    sort_opt_values.append(opt_values[i]/absolute_max_val)
    sort_opt_costs.append(opt_costs[i]/absolute_max_cost)


In [23]:
sort_opt_order

['k80_100x2_4',
 'p4_63x6_4',
 't4_136x4_4',
 'v100_145x6_4',
 'p100_146x4_4',
 'p4_63x8_8',
 't4_136x8_8',
 'p100_146x8_8',
 'v100_145x8_8',
 'p100_145x12_12',
 'v100_145x12_12']

In [24]:
build_graph(sort_opt_order, diff(sort_opt_values), f"Optimized Runtume Waterfall", "optimised")

In [25]:
plt.rcParams.update({'figure.figsize':(64,64), 'figure.dpi':600})
build_graph_w_cost(sort_opt_order, diff(sort_opt_values), diff(sort_opt_costs), f"Optimized: Runtume vs Cost Waterfall", "double")

In [26]:
sort_opt_order

['k80_100x2_4',
 'p4_63x6_4',
 't4_136x4_4',
 'v100_145x6_4',
 'p100_146x4_4',
 'p4_63x8_8',
 't4_136x8_8',
 'p100_146x8_8',
 'v100_145x8_8',
 'p100_145x12_12',
 'v100_145x12_12']

In [27]:
sort_opt_values

[100.00000000000001,
 66.69588195437416,
 66.3844008390352,
 65.86130537895389,
 62.69336951173816,
 54.879097260829425,
 50.24460863171745,
 40.222360667353605,
 34.78307979366869,
 26.47284468451215,
 24.161103023127307]

In [28]:
sort_opt_costs

[36.45645200776485,
 30.001076874169176,
 20.428350893378656,
 100.0,
 58.84472062877664,
 24.685662254731934,
 15.461682001438756,
 42.09674653733872,
 56.56880983068633,
 30.9951634766904,
 42.295442496973386]

In [29]:
#

In [30]:
build_bar_graph_w_cost(sort_opt_order, sort_opt_values, sort_opt_costs, "Optimized: Runtume vs Cost", "optimized_bars.png")

# DRIVER/CUDA PERFORMANCE

In [31]:
df_drv = pd.read_csv(config.data_file)

In [32]:
df_drv = df_drv[(df_drv['gpu_type'] == 't4') & (df_drv['machine_type'] == 'n1-standard-8') & (df_drv['adv_job_params'] == '--batch-size 136 --data-processors 8')]

In [33]:
# df_drv.groupby(['nvidia_driver_major','CUDA']).count()

In [34]:
def get_data(dframe, cuda: str):
    df_drv = dframe[
        (dframe['gpu_type'] == 't4') & \
        (dframe['machine_type'] == 'n1-standard-8') & \
        (dframe['adv_job_params'] == '--batch-size 136 --data-processors 8') & \
        (dframe['CUDA']==cuda)
    ]
    tgb = df_drv.groupby(['nvidia_driver_major',"CUDA"])['runtime']
    y = tgb.mean()
    yerr = tgb.sem()
    label = f'CUDA {cuda[2:]}'
    return y, yerr, label

def get_drv(dframe):
    index = dframe[dframe['CUDA']=='cu10.1'].groupby(['nvidia_driver_major']).first().index.astype('string')
    return index

In [35]:
x = get_drv(df_drv)
print(x)

Index(['410', '418', '440', '450', '455', '460'], dtype='object', name='nvidia_driver_major')


In [40]:
def plot_graph(dframe, inst: str):
    fig = plt.figure()
    ax = fig.subplots()

    mpl.rcParams["errorbar.capsize"] = 5
    mpl.rcParams["figure.titlesize"] = "large"

    x = dframe[dframe['CUDA']=='cu10.1'].groupby(['nvidia_driver_major']).first().index.astype('string')
    y1, yerr1, label1 = get_data(dframe, "cu9.2")
    y2, yerr2, lable2 = get_data(dframe, "cu10.1")
    y3, yerr3, lable3 = get_data(dframe, "cu10.2")
    y4, yerr4, lable4 = get_data(dframe, "cu11.0")

    yerr0 = [0,0,0,0,0,0]

    set1 = plt.errorbar(x, y1, yerr=yerr1, label=label1)
    set1[-1][0].set_linewidth(3)
    # set1[-1][0].set_linestyle('--')

    set2 = plt.errorbar(x, y2, yerr=yerr2, label=lable2)
    set2[-1][0].set_linewidth(3)
    # set2[-1][0].set_linestyle('--')

    set3 = plt.errorbar(x, y3, yerr=yerr3, label=lable3)
    set3[-1][0].set_linewidth(3)
    # set3[-1][0].set_linestyle('--')

    set4 = plt.errorbar(x, y4, yerr=yerr4, label=lable4)
    set4[-1][0].set_linewidth(3)
    # set3[-1][0].set_linestyle('--')

    ax.text(0.2,0.950, GPU[inst], fontdict=titleFondDic, transform = ax.transAxes)
    ax.spines['top'].set_color(None)
    ax.spines['right'].set_color(None)
    ax.spines['left'].set_color(None)
    plt.legend(loc='center left')
    

In [41]:
plot_graph(df_drv, 't4')
plt.savefig(f"images/t4_drv_cuda.png", format="png")

/home/egor/.pipenvs/mlbench/lib/python3.9/site-packages/numpy/core/_asarray.py:102: UserWarning:


